# Notebook Objective and Setup

BGG03 is the scrubbing and cleaning of the various data obtained in notebooks BGG01 and BGG02. The following datasets are cleaned, constructed, or otherwise prepared for EDA and modeling.

    * Games
    * Mechanics
    * Subcategories
    * Designers
    * Artists
    * Publishers
    * Awards
    * Ratings Distribution
    * Comments
    * Ratings Matrix

## Package Imports

In [1]:
import pandas as pd
import numpy as np
import requests
import regex as re
import time
import os
import gc
import json

# ignore warnings (gets rid of Pandas copy warnings)
import warnings
warnings.filterwarnings('ignore')
pd.options.display.max_columns = None

pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', 30)

# NLP tools
import spacy
nlp = spacy.load("en_core_web_sm")
import re
import nltk
from sklearn.feature_extraction.text import CountVectorizer, TfidfVectorizer
from nltk.tokenize import word_tokenize

## Notebook Functions

In [2]:
def integer_reduce(data, columns, fill_value=0):
    '''
    Reduces an integer type to its smallest memory size type
    
    Inputs:
    data: dataframe to reduce
    columns: columns to reduce
    fill_value: fill value to use if none
    
    Returns: 
    data: dataframe with memory reduced data types
    '''
    for column in columns:
        print(column)
        data[column].fillna(fill_value, inplace=True)
        if (data[column].max() <= 127) & (data[column].min() >= -128):
            data[column] = data[column].astype('int8')
        elif (data[column].max() <= 32767) & (data[column].min() >= -32768):
            data[column] = data[column].astype('int16')
        elif (data[column].max() <= 2147483647) & (data[column].min() >= -2147483648):
            data[column] = data[column].astype('int32')
        
    return data

In [3]:
def text_block_processor(text):
    '''Takes a block of text. Divides block into sentences with words lemmatized.
    Sends each sentence to word processor. Concatenates all words into one string
    Otherwise returns string of cleaned and processed words from text block
    
    ARGUMENTS:
    block of text
    '''
    
    text = str(text)
    line = re.sub(r'[^a-zA-Z\s]', '', text).lower() # removes all special characters and numbers, and makes lower case
    line2 = re.sub(r'\s{2}', '', line).lower() # removes extra blocks of 2 spaces
    tokens = nlp(line)
    words = []
    for token in tokens:
        if token.is_stop == False:
            token_preprocessed = token.lemma_
            if token_preprocessed != '': # only continues if returned word is not empty
                words.append(token_preprocessed) # appends word to list of words
    line = ' '.join(words)
    
    return line


In [4]:
def fix_numbers(x):
    '''
    Checks for numbers or strings
    If a string, strips off the "k" and multiply by 10000
    Sends back cleaned int
    '''
    
    if type(x) is int:
        return int(x)
    
    if str.endswith(x, 'k'):
        x = str(x).strip('k')
        new_num = int(float(x)*1000)
        return int(new_num)
    
    else: 
        return int(x)

In [5]:
def clean_ratings(id_num, game_ids):
    '''
    Loads and cleans a raw user ratings file
    Drops game ids not present in games file
    Drops users with fewer than 10 ratings
    
    Inputs:
    id_num: the appendation of the file to find the path
    game_ids: list of game ids in the games file
    
    Outputs:
    Cleaned user ratings file
    '''
    
    print('\nCleaning Frame #'+str(id_num))
    
    #load in raw users file according to id_num inputted
    path = 'userid/user_ratings'+str(id_num)+'.pkl'
    users = pd.read_pickle(path)
    
    # convert all datatypes to float
    float_converted = users.astype('float')
    
    # delete and clean up raw users file
    del users
    gc.collect()
    
    # create intersection between user file and game list ids
    float_converted.columns = float_converted.columns.astype('int32')
    cleaned = float_converted[float_converted.columns.intersection(game_ids)]
    
    # delete and clean up
    del float_converted
    gc.collect()
    
    # make a list of users with fewer than 5 user ratings
    sums = cleaned.count(axis=1)<5
    # get indices for the rows with fewer than 5 ratings
    drop_these = sums.loc[sums==True].index
    # drop the users with fewer than 5 ratings
    cleaned.drop(drop_these, axis=0, inplace=True)
    
    
    # print memory usage
    print(cleaned.info())
    
    # return cleaned file
    return cleaned

In [6]:
def create_ratings_file(start_file, end_file, game_ids):
    '''
    Puts together dataframes from a range of files
    Each file calls the clean_ratings function
    Then all files in range are concatenated
    
    Inputs:
    start_file: start of file name appendation
    end_file: end file name appendation
    game_ids_list: list of game ids in the games file
    
    Outputs:
    Cleaned and concatenated master file
    
    '''
    
    # make an empty dataframe
    master_file = pd.DataFrame()
    
    # for each number in the range from start to end:
    for id_num in np.arange(start_file,end_file+1,1):
        print(id_num)
        # clean the file calling clean_ratings
        cleaned_item = clean_ratings(id_num, game_ids)
        # append the file to the dataframe
        master_file = pd.concat([master_file, cleaned_item], axis=0)
    
    master_file.drop_duplicates(keep='first', inplace=True)
    
    # clean up
    del cleaned_item
    gc.collect()
    
    return master_file

In [8]:
def process_dataframe_ratings(x, user_ratings, raw_ratings):
    
    try:
        user_ratings[x['Username']][x['BGGId']] = float(x['Rating']) 
    
    except:
        user_ratings[x['Username']] = {}
        user_ratings[x['Username']][x['BGGId']] = float(x['Rating']) 
    
    raw_ratings[x['BGGId']].append(x['Rating'])

# Games Files

In [ ]:
games = pd.read_pickle('data_dirty/games.pkl')
games

In [ ]:
games['Theme'].unique()

In [ ]:
# Get info, make note of datatypes and memory usage
games.info()

In [ ]:
#drops = games.loc[games['BGGId']==0].index # get indices of any games with no BGGId
#drops
#games.drop(games.loc[drops].index, axis=0, inplace=True) # drop games with no BGGId

In [ ]:
games.drop_duplicates(subset='BGGId', keep='first', inplace=True) # drop duplicate entires

# drop non-boardgame related information
games.drop(['NumAwards', 'NumFans', 'NumPageViews', 'RulesPosts', 'TotalPosts', 'Category', 'IsExpansion', 'Rank:rpgitem', 'Rank:boardgameaccessory', 'Rank:videogame', 'Rank:amiga', 'Rank:commodore64', 'Rank:arcade', 'Rank:atarist'], axis=1, inplace=True)

games.shape # check shape of file

In [ ]:
# what are the columns?
games.columns

In [ ]:
games['BestPlayers'].fillna(0, inplace=True) # Fill NaN on BestPlayers
games['BestPlayers'].unique() # What are the unique BestPlayers entries?

In [ ]:
# Clean up Best Players so all are integers
games.loc[(games['BestPlayers']=='3+'), 'BestPlayers'] = 3
games.loc[(games['BestPlayers']=='0+'), 'BestPlayers'] = 4

# change dtype on BestPlayers to int8
games['BestPlayers'] = games['BestPlayers'].astype('int8')

In [ ]:
# Add Categories with binary flags
games.loc[games['Rank:thematic'].notna(), 'Cat:Thematic'] = int(1)
games.loc[games['Rank:strategygames'].notna(), 'Cat:Strategy'] = int(1)
games.loc[games['Rank:wargames'].notna(), 'Cat:War'] = int(1)
games.loc[games['Rank:familygames'].notna(), 'Cat:Family'] = int(1)
games.loc[games['Rank:cgs'].notna(), 'Cat:CGS'] = int(1)
games.loc[games['Rank:abstracts'].notna(), 'Cat:Abstract'] = int(1)
games.loc[games['Rank:partygames'].notna(), 'Cat:Party'] = int(1)
games.loc[games['Rank:childrensgames'].notna(), 'Cat:Childrens'] = int(1)

In [ ]:
# prepare different column sets for memory integer reduction

# integer reduction with fill_values of 0
int_columns=['BGGId', 'YearPublished', 'MinPlayers', 'MaxPlayers', 'NumOwned',
       'NumWant', 'NumWish', 'NumWeightVotes', 'MfgPlaytime', 'ComMinPlaytime',
       'ComMaxPlaytime','MfgAgeRec', 'NumUserRatings', 'NumComments',
       'NumAlternates', 'NumExpansions', 'NumImplementations',
       'IsReimplementation', 'Kickstarted', 'Cat:Thematic', 'Cat:Strategy', 
        'Cat:War', 'Cat:Family', 'Cat:CGS', 'Cat:Abstract', 'Cat:Party', 'Cat:Childrens']

# integer reduction with fill_values of 21926 (lower is better on these)
ranks = ['Rank:boardgame', 'Rank:thematic', 'Rank:strategygames',
       'Rank:wargames', 'Rank:familygames', 'Rank:cgs', 'Rank:abstracts',
       'Rank:partygames', 'Rank:childrensgames']

# call integer_reduce on the sets
games = integer_reduce(games, int_columns, fill_value=0)

games = integer_reduce(games, ranks, fill_value=21926)

games.info() # recheck data types and memory usage

In [ ]:
# any games with no name listed?
games.loc[games['Name']==0]

In [ ]:
# if so, drop them and reset index
#empty_games = list(games.loc[games['Name']==0].index)
#games.drop(games.index[empty_games], inplace=True)
#games.reset_index(inplace=True, drop=True)

In [ ]:
# Drop all games that are not yet released, then reset index
#not_released = list(games.loc[games['YearPublished']>2021].index)
#games.drop(games.index[not_released], inplace=True)
#games.reset_index(inplace=True, drop=True)

In [ ]:
# All games with over 12 players are set at 13 players.
games.loc[games['MaxPlayers']>12, 'MaxPlayers'] = 13

In [ ]:
# Games with min players of 0, we will set their min players = 2
games.loc[games['MinPlayers']<1, 'MaxPlayers'] = 2

In [ ]:
themes = pd.DataFrame(games['Theme'])
games.drop('Theme', axis=1, inplace=True)

In [ ]:
# process the Description column text
games['Description'] = games['Description'].apply(lambda x: text_block_processor(x))

In [ ]:
games.reset_index(inplace=True, drop=True)

In [ ]:
# Cleaned and prepared games frame
games

In [ ]:
# save to file
games.to_pickle('data_cleaned_new_scraper/games.pkl')

## Game ID Lookup

In [3]:
# dictionary of game IDs-Names

# Load games
games = pd.read_pickle('data_cleaned/games.pkl')

# lists of game ids and game names
game_ids = list(games['BGGId'])
game_names = list(games['Name'])

# make lookup dictionary
game_id_lookup = {}

# store ids and names in lookup dictionary
for key, item in zip(game_ids, game_names):
    game_id_lookup[key] = item

    
del games
gc.collect()

game_id_lookup

{1: 'Die Macher',
 2: 'Dragonmaster',
 3: 'Samurai',
 4: 'Tal der Könige',
 5: 'Acquire',
 6: 'Mare Mediterraneum',
 7: 'Cathedral',
 8: 'Lords of Creation',
 9: 'El Caballero',
 10: 'Elfenland',
 11: 'Bohnanza',
 12: 'Ra',
 13: 'Catan',
 14: 'Basari',
 15: 'Cosmic Encounter',
 16: 'MarraCash',
 17: 'Button Men',
 18: 'RoboRally',
 19: 'Wacky Wacky West',
 20: 'Full Metal Planète',
 21: 'Gateway to the Stars',
 22: 'Magic Realm',
 23: 'Divine Right',
 24: 'Twilight Imperium',
 25: 'Battlemist',
 26: 'Age of Renaissance',
 27: 'Supremacy: The Game of the Superpowers',
 28: 'Illuminati',
 29: 'Terrain Vague',
 30: 'Dark Tower',
 31: 'Dark World',
 32: 'Buffalo Chess',
 34: 'Arkham Horror',
 36: 'Federation & Empire',
 37: 'Dragon Masters',
 38: 'Runes',
 39: 'Darkover',
 40: 'Borderlands',
 41: "Can't Stop",
 42: 'Tigris & Euphrates',
 43: 'Airlines',
 44: 'David & Goliath',
 45: 'Perudo',
 46: 'Medici',
 47: 'Chinatown',
 48: 'Krieg und Frieden',
 49: 'Mamma Mia!',
 50: 'Lost Cities',
 

In [4]:
# save dictionary
with open('data_cleaned/game_id_lookup.json', 'w') as convert_file:
    convert_file.write(json.dumps(game_id_lookup))

## Mechanics and Subcategories

### Load and Clean Mechanics

In [ ]:
# Load mechanics and check memory usage
mechanics = pd.read_pickle('data_dirty/mechanics.pkl')
mechanics

In [ ]:
mechanics.drop_duplicates(subset='BGGId', keep='first', inplace=True)  # drop duplicates
mechanics.fillna(0, inplace=True) # fill nan

mechanics.reset_index(inplace=True, drop=True) # reset index
mechanics.info() # check memory usage

In [ ]:
# Clean up mechanics
# Here we are using our domain knowledge to compact several different catogories into one

auction_list = ['Auction: Dexterity','Auction: Dutch','Auction: Dutch Priority',
                'Auction: Fixed Placement','Auction: English','Auction: Once Around','Auction: Sealed Bid',
                'Auction: Turn Order Until Pass','Multiple-Lot Auction','Closed Economy Auction','Selection Order Bid',
                'Constrained Bidding']

turn_order_list = ['Turn Order: Auction','Turn Order: Claim Action','Turn Order: Pass Order',
                   'Turn Order: Progressive','Turn Order: Random','Turn Order: Role Order','Turn Order: Stat-Based']

dumb_physical_list = ['Acting','Hot Potato','Singing','Rock-Paper-Scissors']

drafting = ['Card Drafting']

legacy = ['Legacy']

worker_placement = ['Worker Placement with Dice Workers','Worker Placement, Different Worker Types'] #'Worker Placement',

dexterity = ['Stacking and Balancing', 'Flicking']

# compacting categories here:

for item in worker_placement:
    mechanics.loc[mechanics[item]==1, 'Worker Placement'] = int(1)
    mechanics.drop([item], axis=1, inplace=True)

for item in auction_list:
    mechanics.loc[mechanics[item]==1, 'Auction/Bidding'] = int(1)
    mechanics.drop([item], axis=1, inplace=True)

mechanics['Dexterity'] = int(0)
for item in dexterity:
    mechanics.loc[mechanics[item]==1, 'Dexterity'] = int(1)
    mechanics.drop([item], axis=1, inplace=True)
    
mechanics['Physical'] = int(0)
for item in dumb_physical_list:
    mechanics.loc[mechanics[item]==1, 'Physical'] = int(1)
    mechanics.drop([item], axis=1, inplace=True)
    
mechanics.loc[mechanics['Card Drafting']==1, 'Drafting'] = int(1)

mechanics.loc[mechanics['Legacy']==1, 'Legacy Game'] = int(1)

mechanics.drop(turn_order_list, axis=1, inplace=True)
mechanics.drop(['Card Drafting','Legacy'], axis=1, inplace=True)

In [ ]:
columns = mechanics.columns

# call integer_reduce on the sets
mechanics = integer_reduce(mechanics, columns, fill_value=0)

In [ ]:
mechanics

### Load and Clean Subcategories

In [ ]:
themes_expanded = pd.get_dummies(themes)
theme_sort = pd.DataFrame(themes_expanded.sum().sort_values(ascending=False))
themes_over_1 = list(theme_sort.loc[theme_sort[0]>1].index)
themes_attach = themes_expanded[themes_over_1]
themes_attach

In [ ]:
columns = themes_attach.columns

# call integer_reduce on the sets
themes_attach = integer_reduce(themes_attach, columns, fill_value=0)

In [ ]:
# load subcategories file and check memory usage

indices = list(games['BGGId'])
subcategories = pd.read_pickle('data_dirty/subcategories.pkl')
subcategories.info()

In [ ]:
subcategories.reset_index(inplace=True, drop=True) # reset index

In [ ]:
subcategories.drop_duplicates(subset='BGGId', keep='first', inplace=True) # drop duplicates
subcategories.fillna(0, inplace=True) # fill nan
#subcategories.set_index('BGGId', drop=True, inplace=True) # drop bad games
#subcategories = subcategories.loc[indices] # use only indices in games file

columns = subcategories.columns

# call integer_reduce on the sets
subcategories = integer_reduce(subcategories, columns, fill_value=0)


subcategories

### Clean/Combine Mechanics and Subcategories

Manually cleaning up Subcategories. This section on BGG has a lot of "catch-all" concept that involve theming, mechanics (which should be in the mechanics section), and large subcategories that should be alone. We use our domain knowledge to clean this section.

In [ ]:
# print our subcategories so we can prepare to sort them
subcategories.columns

In [ ]:
# picking the items that will go under "themes"
subcats_themes = ['BGGId', 'Adventure', 'Fantasy', 'Fighting', 'Environmental', 'Medical', 'Economic',
       'Industry / Manufacturing', 'Transportation', 'Science Fiction',
       'Space Exploration', 'Civilization', 'Civil War',
       'Movies / TV / Radio theme', 'Novel-based',
       'Age of Reason', 'Mythology', 'Renaissance', 'American West', 'Animals',
       'Modern Warfare', 'Medieval', 'Ancient','Nautical', 'Post-Napoleonic', 'Horror',
         'Farming', 'Religious', 'Travel',
       'Murder/Mystery', 'Pirates', 'Comic Book / Strip', 'Mature / Adult',
       'Video Game Theme', 'Spies/Secret Agents','Arabian', 'Prehistoric',
                 'Trains','Aviation / Flight', 'Zombies',
       'World War II', 'Racing', 'Pike and Shot', 'World War I','Humor','Sports',
                 'Mafia','American Indian Wars', 'Napoleonic',
       'American Revolutionary War','Vietnam War', 'American Civil War','Number', 'Trivia',
       'Music', 'Korean War', 'City Building', 'Political', 'Math', 'Maze',]

In [ ]:
# picking the items that will stay as subcategories
subcats_subcategories = ['BGGId', 'Exploration', 'Miniatures', 'Territory Building', 'Card Game',
             'Educational', 'Puzzle','Collectible Components',
        'Word Game','Print & Play','Electronic']

In [ ]:
# looking at our mechanics in alphabetical order so we can see where to roll in the subcategory mechanics
sorted(mechanics.columns)

In [ ]:
# drop subcategories that are none of the things
subcategories.drop(['Expansion for Base-game',  'Game System', 'Book'], axis=1, inplace=True)

In [ ]:
# for mechanics that are mistakenly in the subcategories frame, make sure those mechanics are in the mechanics frame instead
# remove them from the subcategories frame after moving them over

indices = list(subcategories.loc[subcategories['Negotiation']==1].index)
mechanics.loc[indices, 'Negotiation']=1
subcategories.drop('Negotiation', axis=1, inplace=True)

indices = list(subcategories.loc[subcategories['Action / Dexterity']==1].index)
mechanics.loc[indices, 'Dexterity']=1
subcategories.drop('Action / Dexterity', axis=1, inplace=True)

indices = list(subcategories.loc[subcategories['Dice']==1].index)
mechanics.loc[indices, 'Dice Rolling']=1
subcategories.drop('Dice', axis=1, inplace=True)

indices = list(subcategories.loc[subcategories['Bluffing']==1].index)
mechanics.loc[indices, 'Betting and Bluffing']=1
subcategories.drop('Bluffing', axis=1, inplace=True)

indices = list(subcategories.loc[subcategories['Real-time']==1].index)
mechanics.loc[indices, 'Real-Time']=1
subcategories.drop('Real-time', axis=1, inplace=True)

indices = list(subcategories.loc[subcategories['Memory']==1].index)
mechanics.loc[indices, 'Memory']=1
subcategories.drop('Memory', axis=1, inplace=True)

indices = list(subcategories.loc[subcategories['Deduction']==1].index)
mechanics.loc[indices, 'Deduction']=1
subcategories.drop('Deduction', axis=1, inplace=True)


In [ ]:
# or for larger categories in the subcategories frame, move those to the games frame
# remove them from the subcategories frame after moving them over

indices = list(subcategories.loc[subcategories['Wargame']==1].index)
games.loc[indices, 'Cat:War']=1
subcategories.drop('Wargame', axis=1, inplace=True)

indices = list(subcategories.loc[subcategories["Children's Game"]==1].index)
games.loc[indices, 'Cat:Childrens']=1
subcategories.drop("Children's Game", axis=1, inplace=True)

indices = list(subcategories.loc[subcategories['Party Game']==1].index)
games.loc[indices, 'Cat:Party']=1
subcategories.drop('Party Game', axis=1, inplace=True)

indices = list(subcategories.loc[subcategories['Abstract Strategy']==1].index)
games.loc[indices, 'Cat:Abstract']=1
subcategories.drop('Abstract Strategy', axis=1, inplace=True)

In [ ]:
# make new data frames for THEMES and SUBCATEGORIES
themes = subcategories[subcats_themes]
themes = pd.concat([themes, themes_attach], axis=1)
subcategories = subcategories[subcats_subcategories]

Save all the file we just cleaned or created!

In [ ]:
mechanics.to_pickle('data_cleaned_new_scraper/mechanics.pkl')

In [ ]:
subcategories.to_pickle('data_cleaned_new_scraper/subcategories.pkl')

In [ ]:
themes.to_pickle('data_cleaned_new_scraper/themes.pkl')

## Designers

In [ ]:
# Load up our designers file!
designers = pd.read_pickle('data_dirty/designers.pkl')
designers.info()

In [ ]:
designers.drop_duplicates(subset='BGGId', keep='first', inplace=True) # drop duplicates
designers.fillna(0, inplace=True) # Fill NaN

# change all flags to int8
temp_id = designers['BGGId'] 
designers.drop('BGGId', axis=1, inplace=True)
designers = designers.astype('int8')
designers['BGGId'] = temp_id

designers.reset_index(inplace=True, drop=True)# reset index
designers.info() # check memory usage

In [ ]:
# save file of all possible designers
designers.to_pickle('data_cleaned_new_scraper/designers_all.pkl')

In [ ]:
# locate all row that sum to 3 or less (find low experience designers)

# change the 3 to whatever desired for more or less experience
lowexp_rows = designers.loc[:, designers.sum(axis=0) <= 3]

# Locate the columns that contain the low experience designers
lowexp_columns = lowexp_rows[lowexp_rows.sum(axis=1) > 0]

# get indices of those low-exp columns
indices = lowexp_columns.index

# make new column for low exp designer
designers['Low-Exp Designer'] = 0

# for each index in the low exp list, set low exp designer to 1
for index in indices:
    designers.loc[index, 'Low-Exp Designer'] = 1
    
# drop all columns for one-off designers
designers.drop(designers.loc[:, designers.sum(axis=0) <= 3], axis=1, inplace=True)

In [ ]:
# save file of designers reduced to 3 or more works
designers.to_pickle('data_cleaned_new_scraper/designers_reduced.pkl')

## Artists

In [ ]:
# load artists file
artists = pd.read_pickle('data_dirty/artists.pkl')
artists.info()

In [ ]:
artists.drop_duplicates(subset='BGGId', keep='first', inplace=True) # drop duplicates
artists.fillna(0, inplace=True) # fill nan

# convert flags to int8
temp_id = artists['BGGId']
artists.drop('BGGId', axis=1, inplace=True)
artists = artists.astype('int8')
artists['BGGId'] = temp_id

artists.reset_index(inplace=True, drop=True)# reset index
artists.info()# get memory usage

In [ ]:
# save all artists to file
artists.to_pickle('data_cleaned_new_scraper/artists_all.pkl')

In [ ]:
# locate all row that sum to 3 or less (find low experience artists)

# change the 3 to whatever desired for more or less experience
lowexp_rows = artists.loc[:, artists.sum(axis=0) <= 3]

# Locate the columns that contain the low experience artists
lowexp_columns = lowexp_rows[lowexp_rows.sum(axis=1) > 0]

# get indices of those low-exp columns
indices = lowexp_columns.index

# make new column for low exp Artist
artists['Low-Exp Artist'] = 0

# for each index in the low exp list, set low exp Artist to 1
for index in indices:
    artists.loc[index, 'Low-Exp Artist'] = 1
    
# drop all columns for one-off artists
artists.drop(artists.loc[:, artists.sum(axis=0) <= 3], axis=1, inplace=True)

In [ ]:
# save artists to file reduces to 3 or more works
artists.to_pickle('data_cleaned_new_scraper/artists_reduced.pkl')

## Publishers

In [ ]:
# load publishers
publishers = pd.read_pickle('data_dirty/publishers.pkl')
publishers.info()

In [ ]:
publishers.drop_duplicates(subset='BGGId', keep='first', inplace=True) # drop duplicates
publishers.fillna(0, inplace=True)# fill nan

# set flags to int8
temp_id = publishers['BGGId']
publishers.drop('BGGId', axis=1, inplace=True)
publishers = publishers.astype('int8')
publishers['BGGId'] = temp_id

publishers.reset_index(inplace=True, drop=True) # reset index
publishers.info() # get memory usage

In [ ]:
# save all publishers to file
publishers.to_pickle('data_cleaned_new_scraper/publishers_all.pkl')

In [ ]:
# locate all row that sum to 3 or less (find low experience publishers)

# change the 3 to whatever desired for more or less experience
lowexp_rows = publishers.loc[:, publishers.sum(axis=0) <= 3]

# Locate the columns that contain the low experience publishers
lowexp_columns = lowexp_rows[lowexp_rows.sum(axis=1) > 0]

# get indices of those low-exp columns
indices = lowexp_columns.index

# make new column for low exp Publisher
publishers['Low-Exp Publisher'] = 0

# for each index in the low exp list, set low exp Publisher to 1
for index in indices:
    publishers.loc[index, 'Low-Exp Publisher'] = 1
    
# drop all columns for one-off publishers
publishers.drop(publishers.loc[:, publishers.sum(axis=0) <= 3], axis=1, inplace=True)

In [ ]:
# save publishers reduced to 3 or more works
publishers.to_pickle('data_cleaned_new_scraper/publishers_reduced.pkl')

# Ratings - by Item, User, & Comments

## Test Code

In [17]:
master_comments = pd.read_pickle('data_dirty/raw_game_ratings.pkl')

# integer_reduce
master_comments['BGGId'] = master_comments['BGGId'].astype(int)
master_comments['Rating'] = master_comments['Rating'].astype(float)

master_comments.head()

BGGId                                       Name     Username  Rating  \
0  213788  Ascension: Year Three Collector's Edition    Tonydorrf     8.0   
1  213788  Ascension: Year Three Collector's Edition   tachyon14k     8.0   
2  213788  Ascension: Year Three Collector's Edition     Ungotter     8.0   
3  213788  Ascension: Year Three Collector's Edition  brainlocki3     8.0   
4  213788  Ascension: Year Three Collector's Edition         PPMP     8.0   

  Comments  
0           
1           
2           
3           
4

In [18]:
master_comments.drop_duplicates(keep='first', inplace=True)

In [19]:
master_comments.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 18954963 entries, 0 to 62419
Data columns (total 5 columns):
 #   Column    Dtype  
---  ------    -----  
 0   BGGId     int32  
 1   Name      object 
 2   Username  object 
 3   Rating    float64
 4   Comments  object 
dtypes: float64(1), int32(1), object(3)
memory usage: 795.4+ MB


In [31]:
nodrops = list(master_comments.loc[master_comments.Comments!=''].index)

In [32]:
comments_only = master_comments.iloc[nodrops]

In [36]:
comments_only.head(10)

BGGId                                       Name       Username  Rating  \
5   213788  Ascension: Year Three Collector's Edition     Dychotimer     8.0   
14  213788  Ascension: Year Three Collector's Edition      Narstrand     7.8   
27  213788  Ascension: Year Three Collector's Edition     bassgonist     7.0   
28  213788  Ascension: Year Three Collector's Edition     SpaceAlien     7.0   
29  213788  Ascension: Year Three Collector's Edition  stormseeker75     7.0   
34  213788  Ascension: Year Three Collector's Edition       Paletius     7.0   
43  213788  Ascension: Year Three Collector's Edition         Acward     7.0   
45  213788  Ascension: Year Three Collector's Edition       hatbeard     7.0   
47  213788  Ascension: Year Three Collector's Edition    Chunkmonger     7.0   
53  213788  Ascension: Year Three Collector's Edition   DurangoExile     7.0   

                                             Comments  
5   Excellent Ascension that now are all full sets...  
14  Fantastic deck builder! The quality of the Col...  
27  Only contains 40 energy shards and 10 dark ene...  
28                        Plus King Rat promo cards.   
29  I really don't like the Energy cards in here s...  
34  I didn't enjoy this one as much as the year tw...  
43  We definitely enjoy owning this for the wonder...  
45               Current Location: Brighton Solo: Yes  
47  The art has improved since it's first release....  
53  Nice deck building game with very few rough ed...

In [34]:
comments_only.to_pickle('data_cleaned/master_comments_file.pkl')

In [39]:
del comments_only
gc.collect()

210

## Deploy - User and Item Ratings

In [37]:
raw_game_ratings = pd.read_pickle('data_dirty/raw_game_ratings.pkl')

In [38]:
ratings = raw_game_ratings[['BGGId', 'Rating', 'Username']]
ratings.head()

BGGId  Rating     Username
0  213788     8.0    Tonydorrf
1  213788     8.0   tachyon14k
2  213788     8.0     Ungotter
3  213788     8.0  brainlocki3
4  213788     8.0         PPMP

In [40]:
del raw_game_ratings
gc.collect()

21

In [41]:
ratings.drop_duplicates(keep='first', inplace=True)

In [42]:
game_ids_current = pd.read_pickle('data_cleaned/game_ids_current.pkl')
game_ids = list(game_ids_current)

In [43]:
user_ratings = {}

raw_ratings = {}

for item in game_ids:
    raw_ratings[item] = []

In [44]:
ratings.apply(lambda x: process_dataframe_ratings(x, user_ratings, raw_ratings), axis=1)

0        None
1        None
2        None
3        None
4        None
         ... 
62415    None
62416    None
62417    None
62418    None
62419    None
Length: 18942215, dtype: object

In [45]:
user_ratings['Threnody']

{25190: 6.0,
 13: 6.0,
 3076: 6.0,
 822: 7.0,
 68448: 7.5,
 2651: 6.0,
 30549: 8.0,
 31260: 7.0,
 14996: 7.0,
 266192: 7.0,
 110327: 7.0,
 9209: 7.0,
 70323: 7.0,
 36218: 8.0,
 28143: 7.0,
 34635: 7.0,
 178900: 8.0,
 237182: 7.0,
 162886: 7.0,
 167791: 9.0,
 98778: 7.0,
 320: 4.0,
 201808: 7.0,
 41114: 7.0,
 230802: 8.0,
 124361: 7.5,
 18602: 7.0,
 157354: 7.5,
 169786: 9.0,
 148228: 8.0,
 65244: 7.0,
 1406: 3.0,
 157969: 7.0,
 170216: 8.0,
 146508: 6.5,
 37111: 8.0,
 129622: 8.0,
 224517: 8.0,
 50: 7.0,
 10547: 7.0,
 478: 7.5,
 11: 7.0,
 40834: 8.0,
 3955: 6.0,
 118: 6.0,
 199792: 8.0,
 291457: 8.0,
 27162: 7.0,
 50381: 6.0,
 2453: 7.0,
 192291: 7.5,
 3: 6.0,
 233867: 7.5,
 218603: 7.0,
 43443: 6.0,
 172818: 6.5,
 1294: 5.0,
 124708: 7.0,
 182028: 9.0,
 244521: 8.0,
 239188: 7.5,
 182874: 7.5,
 37046: 7.5,
 148949: 8.0,
 102652: 7.0,
 131357: 8.0,
 219513: 7.0,
 199561: 8.0,
 2921: 2.0,
 9216: 6.0,
 155426: 8.0,
 236457: 8.0,
 220877: 6.5,
 104006: 8.0,
 247763: 8.0,
 198994: 7.0,
 19

In [46]:
raw_ratings[213788]

[8.0,
 8.0,
 8.0,
 8.0,
 8.0,
 8.0,
 8.0,
 8.0,
 8.0,
 8.0,
 8.0,
 8.0,
 8.0,
 8.0,
 7.8,
 7.6,
 7.50667,
 7.5,
 7.5,
 7.5,
 7.5,
 7.5,
 7.2,
 7.0,
 7.0,
 7.0,
 7.0,
 7.0,
 7.0,
 7.0,
 7.0,
 7.0,
 7.0,
 7.0,
 7.0,
 7.0,
 7.0,
 7.0,
 7.0,
 7.0,
 7.0,
 7.0,
 7.0,
 7.0,
 7.0,
 7.0,
 7.0,
 7.0,
 7.0,
 7.0,
 7.0,
 7.0,
 7.0,
 7.0,
 6.77778,
 6.5,
 6.5,
 6.5,
 6.0,
 6.0,
 6.0,
 6.0,
 6.0,
 6.0,
 6.0,
 6.0,
 6.0,
 6.0,
 5.0,
 5.0,
 5.0,
 4.0,
 4.0,
 3.0,
 1.5,
 10.0,
 10.0,
 10.0,
 10.0,
 10.0,
 10.0,
 10.0,
 10.0,
 10.0,
 10.0,
 10.0,
 10.0,
 10.0,
 10.0,
 10.0,
 10.0,
 10.0,
 10.0,
 10.0,
 10.0,
 10.0,
 10.0,
 10.0,
 10.0,
 10.0,
 10.0,
 10.0,
 10.0,
 10.0,
 9.02312,
 9.0,
 9.0,
 9.0,
 9.0,
 9.0,
 9.0,
 9.0,
 9.0,
 9.0,
 9.0,
 9.0,
 9.0,
 9.0,
 9.0,
 9.0,
 9.0,
 9.0,
 9.0,
 9.0,
 9.0,
 9.0,
 9.0,
 9.0,
 9.0,
 9.0,
 9.0,
 9.0,
 9.0,
 9.0,
 9.0,
 9.0,
 9.0,
 8.9,
 8.8,
 8.5,
 8.5,
 8.5,
 8.5,
 8.5,
 8.5,
 8.3,
 8.0,
 8.0,
 8.0,
 8.0,
 8.0,
 8.0,
 8.0,
 8.0,
 8.0,
 8.0,
 8.0,
 8.0,
 8.0,
 8.0,

In [47]:
# save dictionary
with open('data_cleaned/game_raw_ratings.json', 'w') as convert_file:
    convert_file.write(json.dumps(raw_ratings))
    
with open('real_ratings/user_ratings_unscaled.json', 'w') as convert_file:
    convert_file.write(json.dumps(user_ratings))
    
del ratings
gc.collect() 

0

### Winnow Users to 5+ Ratings

In [ ]:
# Opening JSON file
with open('data_cleaned/user_ratings_unscaled.json') as json_file:
    user_ratings = json.load(json_file)

In [48]:
all_users = list(user_ratings.keys())

In [49]:
for user in all_users:

    if len(user_ratings[user]) < 5:
        print("Removing user "+user)
        del user_ratings[user]
        continue

Removing user cdlbear
Removing user SteelGoat
Removing user purma
Removing user Pelike
Removing user razclep27
Removing user TheBoardroomGuelph
Removing user kratos4ever
Removing user Mulufuf
Removing user dsfmagalhaes2
Removing user fripp21
Removing user Tanathliath
Removing user Enrique74
Removing user big game nerd
Removing user bgbeat
Removing user Jpm72
Removing user mkolakow
Removing user loutre_on_fire
Removing user bluefunoodle311
Removing user lubo2308
Removing user Omnievul
Removing user Freikonier
Removing user SayethWe
Removing user piemaster42
Removing user ginesjo
Removing user krayzjake
Removing user Gonzo72420
Removing user frappe67
Removing user Bailen
Removing user tablandford
Removing user radperia
Removing user Nachi22
Removing user GentleGiant
Removing user biechou
Removing user galactic_echidna
Removing user kjshier
Removing user crozey
Removing user SawtoothPike
Removing user xuMuk
Removing user AndarWorld
Removing user Dystopie
Removing user cjwallington
Removin

Removing user rlrthesecond
Removing user Miltrez
Removing user Ballroom_Boy
Removing user SmutsMuts
Removing user DarkCrisis
Removing user Portz1986
Removing user Jounieh
Removing user Sisco602
Removing user Reddo1970
Removing user cdhouse
Removing user Marcanton80
Removing user ahab105
Removing user psyberwyche
Removing user JerryA92656
Removing user CommissarHarris
Removing user Wango Guppy
Removing user daddiostan
Removing user cerebrergames
Removing user Troemck
Removing user DBL07
Removing user karmictraveler
Removing user LordMomonga
Removing user tjhsu
Removing user Ariel Kitsune
Removing user PCsajbok
Removing user spijs
Removing user Frejay
Removing user plamitzer
Removing user mli1180
Removing user calllithrix
Removing user smartermonkey
Removing user ourex
Removing user Narcissa
Removing user rafiki03
Removing user Tamawi
Removing user Markos
Removing user trendy11one
Removing user RichardMaly
Removing user Arcanist Lupus
Removing user Ahruk
Removing user rmalena
Removing us

Removing user MailMan37
Removing user qtpiepagan
Removing user Silvanus4031
Removing user Jack_Dawkins
Removing user minasdelrey
Removing user Torvapor
Removing user CallieMo
Removing user Frizank9009
Removing user RadFireGames
Removing user BrettSpieler123
Removing user tkstorm7777
Removing user TheSolecist
Removing user NathanMeunier
Removing user Fungisi
Removing user RosswellSA
Removing user Zdeiv
Removing user cakey77
Removing user Jamem2000
Removing user KerryM
Removing user aodk
Removing user Brandborg
Removing user Grkm
Removing user Christia
Removing user Gazsibacsi
Removing user MWPayne
Removing user tchalla
Removing user milkcrate_junk
Removing user Peardotdash
Removing user TantrumStudioJ
Removing user Shinotama
Removing user SergiSan
Removing user sduque942
Removing user sabrinabgg
Removing user Haiku6810
Removing user gellemar
Removing user kaelari
Removing user Jerry DeMoss
Removing user ulysisgrunt
Removing user hambobulous
Removing user android0025
Removing user Stealt

Removing user gw5097
Removing user dk_sou
Removing user Major Nygren
Removing user guibest
Removing user batchwest
Removing user ThibaultVillaret
Removing user hongtai
Removing user kyung_ryun
Removing user Charlick
Removing user louisirosenthal
Removing user kensweet
Removing user dana buckley
Removing user FlyMeToTheMoon
Removing user wolfy86
Removing user Eken
Removing user wraith2021
Removing user Hands 
Removing user jam920
Removing user BayouJack
Removing user eltrader64
Removing user Rick4866
Removing user jbl7979
Removing user mountainman
Removing user Vetrarbreytin
Removing user CRFout
Removing user Fleeg
Removing user p3t3r
Removing user CarromNut
Removing user Rob_W
Removing user goocon
Removing user asymcomp
Removing user Gramps
Removing user jqdeacon
Removing user cheenlong168
Removing user silvermist
Removing user Aured
Removing user rafal_b1
Removing user mfatih
Removing user SMaithei
Removing user abused solution
Removing user EchoTwoZero
Removing user Jakethornton
Remo

Removing user screagle
Removing user dziambel
Removing user AntoniusPrime
Removing user Tonib_76
Removing user JandoIsKing
Removing user Lcuz
Removing user sekritsnek
Removing user Chikori
Removing user Abesszin
Removing user Arsinoe79
Removing user Gamear
Removing user Soundfield
Removing user ZedIsDeadd
Removing user livyaara
Removing user ArveD
Removing user ingelis
Removing user DanielMue
Removing user Aendi
Removing user Vanna
Removing user nsa4ever
Removing user Templtom
Removing user golikua
Removing user dvunkannon
Removing user yairlem
Removing user rockbottoms
Removing user XenoCyber
Removing user yakmor
Removing user omrir
Removing user Imri_Halpert
Removing user muskiteru
Removing user DRFuzzyFace
Removing user OrenShainin
Removing user TR72
Removing user Siladon
Removing user natan_shtockhammer
Removing user keldath
Removing user hulkenergy
Removing user Heldenschmiede
Removing user marskeiko
Removing user travelphotolady
Removing user MalignantSlug
Removing user c_dog
Rem

...

Removing user naomh76
Removing user eselwin
Removing user Gary1
Removing user Dralex777
Removing user Jkpgamer
Removing user babba111
Removing user skostka21
Removing user Kent Forry
Removing user sweetkiwi
Removing user pontz
Removing user Lammarrrrrrr
Removing user Lamora2018
Removing user chtitphilou
Removing user MarsVoltaic
Removing user yanomake
Removing user Cein
Removing user kalledesu
Removing user Cunix85
Removing user Castir
Removing user MaybeAnApple
Removing user StoneyBraves
Removing user Smarrel
Removing user raizy
Removing user Louiminator
Removing user Clazone
Removing user DarkMeku
Removing user TheBlackSet
Removing user srbm
Removing user rs555
Removing user Donutello
Removing user GerBalz
Removing user SauZucht
Removing user CelestialRuler
Removing user Galkalah
Removing user Biene_
Removing user Daniele_Seghizzi
Removing user Omegabeat
Removing user reqv
Removing user Jeffel
Removing user SuchPaint_Wow
Removing user Arestales
Removing user Tashijan
Removing user ka

Removing user kungfuquickness
Removing user theredranger8
Removing user mcanderson1121
Removing user bp_th
Removing user Storyweaver17
Removing user miketheredherring
Removing user Stridersoa
Removing user Gmoney72
Removing user Uvspyro
Removing user BOF007
Removing user lunahex
Removing user Skwuruhl
Removing user hyoen
Removing user codeone
Removing user FireOfGold
Removing user iimthomas
Removing user RedlacOiar
Removing user dseemonster
Removing user igcase1996
Removing user Kyra Darkblood
Removing user abufisaril
Removing user SawedeSVK
Removing user StrikeIT
Removing user gazza006
Removing user Lavinak
Removing user magicari
Removing user MainGamer
Removing user thingsrlooknup
Removing user Dark4ce
Removing user wsheph
Removing user nzwargamer
Removing user RatonLover
Removing user LordRossatron
Removing user Caderyn
Removing user jamis
Removing user Kraylore
Removing user DerVigilante
Removing user Dragombre
Removing user Alfredocorleone
Removing user abeal28
Removing user InViv

Removing user foxotrox
Removing user 50ShadesOfGames
Removing user Sudomiser
Removing user Spyrakoonz
Removing user Juls_v
Removing user valenson
Removing user channum
Removing user Hithoel
Removing user pvoss07
Removing user MalteMink
Removing user HaloJill
Removing user shamefulsquid
Removing user chartmapcounter
Removing user warlord_craig
Removing user Jajan1
Removing user angelgarcia
Removing user DCWilly
Removing user TheVmo
Removing user Edwarder
Removing user Claidheamdanns
Removing user Fimb
Removing user jabbadabbadoo
Removing user Fridagreen
Removing user annabannana
Removing user Default Printer
Removing user Sir_Lancelot888
Removing user Snowwalker1966
Removing user chefa_13
Removing user forgottenlore666
Removing user Yoyo37230
Removing user TrollWood
Removing user Sleestak999
Removing user blackmonk17
Removing user jarwiecz
Removing user Mill8811
Removing user Imytho
Removing user halus
Removing user glittergirl
Removing user wayneheeley
Removing user mbortel
Removing us

Removing user mattjgilbert
Removing user tyrela
Removing user Machinegunjoe
Removing user ghostmachine
Removing user Aunu
Removing user Bealek
Removing user scarloxk
Removing user Ared Mosinel
Removing user Acika1991
Removing user 27mad5aled
Removing user Alistair Hutton
Removing user Karnivor
Removing user Galilee
Removing user Yoshipl
Removing user neocaptain
Removing user QQrydz
Removing user Frayser
Removing user izhang05
Removing user Olzenstein
Removing user Riverhorse
Removing user pomme62
Removing user shershot
Removing user hughathompson
Removing user Kjos7
Removing user Ironmatt2000
Removing user TehFoxdonut
Removing user Doomguy2112
Removing user Crockett1836
Removing user Robdguk
Removing user DerekHupp
Removing user andymk
Removing user yllet
Removing user thomasson90
Removing user michnils
Removing user heddena
Removing user maneki1000
Removing user bpovio
Removing user mf304999
Removing user PhantomHunter
Removing user loadedchicken
Removing user padewan
Removing user So

Removing user mbauers
Removing user Prattlesnake
Removing user SmoothCriminal15
Removing user 23axisandallie
Removing user Travelingarmadillo
Removing user Vipergecko03
Removing user Ormagon
Removing user CJ22
Removing user jigglywamp
Removing user Mark19833
Removing user Gaelan88
Removing user L_innominabile
Removing user corvegeta
Removing user whisperingshadow
Removing user starchildren
Removing user Mcrush
Removing user Whounsome
Removing user Kapetaum
Removing user fullerba
Removing user gardneremail
Removing user bobthethird
Removing user Nirsh
Removing user dyskamipublishing
Removing user Jmaczek
Removing user Ansgar74
Removing user jkuboschek
Removing user JRDOZ
Removing user Aristore
Removing user nicholashay1989
Removing user FlakManiak
Removing user etwasa
Removing user denonde
Removing user Konjo89
Removing user YagoPepper
Removing user hammerdf
Removing user rxpbr
Removing user bubarad
Removing user momorad
Removing user pizzapollo82
Removing user TrueLink
Removing user Ol

In [50]:
with open('data_cleaned/user_ratings_unscaled.json', 'w') as convert_file:
    convert_file.write(json.dumps(user_ratings))

## Ratings Distribution

In [52]:
# Load the storage dictionary for this block
with open('data_cleaned/game_raw_ratings.json') as json_file:
    raw_ratings = json.load(json_file) 

In [53]:
len(raw_ratings)

21925

In [54]:
ratings_distribution = pd.DataFrame()

for item in raw_ratings.keys():
    
    print(item)
    
    ratings_temp = pd.DataFrame(raw_ratings[item]).round(1)
    ratings_counts = pd.DataFrame(ratings_temp.value_counts()).sort_index().T
    
    ratings_distribution = ratings_distribution.append(ratings_counts)

1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
34
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
57
58
59
60
61
62
63
64
66
67
68
69
70
71
72
73
74
75
76
77
78
79
82
83
84
85
87
88
89
90
91
93
94
95
96
97
98
99
101
102
103
104
105
106
108
109
110
111
112
113
114
115
116
117
118
119
120
121
122
124
125
126
127
128
130
132
133
134
135
136
137
139
140
141
142
144
145
146
147
148
150
151
152
153
154
155
156
157
162
163
164
165
166
167
168
169
170
171
172
173
174
175
176
178
179
180
181
182
183
185
186
188
189
190
192
193
194
195
196
197
198
199
200
201
202
204
206
207
208
210
211
214
215
216
217
218
219
220
221
222
223
224
225
226
228
229
230
231
232
234
235
237
239
240
241
242
243
244
246
247
248
249
250
252
254
255
256
257
258
259
260
261
263
264
265
267
268
270
271
272
273
274
275
276
277
278
279
280
281
282
283
284
285
286
287
288
289
290
291
292
293
294
295
296
297
298
299
300
301
302
303
304
305
307
308
309
310
311
312
313
314
315


2573
2574
2577
2578
2579
2580
2581
2582
2583
2584
2586
2589
2593
2596
2597
2598
2599
2600
2602
2603
2604
2605
2606
2607
2608
2609
2610
2611
2612
2613
2616
2625
2626
2627
2629
2630
2633
2634
2635
2637
2638
2639
2640
2641
2643
2645
2649
2650
2651
2652
2653
2655
2656
2657
2664
2665
2666
2667
2668
2669
2672
2674
2676
2678
2679
2680
2681
2688
2689
2690
2693
2697
2698
2699
2701
2705
2706
2707
2709
2710
2713
2716
2717
2718
2719
2720
2721
2724
2725
2728
2730
2731
2733
2734
2736
2738
2740
2742
2743
2746
2748
2749
2750
2751
2753
2756
2757
2758
2759
2760
2762
2763
2764
2765
2766
2767
2770
2771
2773
2775
2776
2777
2778
2779
2780
2781
2782
2783
2784
2785
2788
2791
2792
2793
2794
2795
2799
2800
2802
2806
2808
2809
2811
2812
2814
2816
2817
2818
2819
2821
2823
2824
2826
2832
2833
2836
2838
2839
2840
2841
2842
2843
2844
2845
2853
2854
2855
2856
2857
2858
2860
2863
2864
2866
2867
2868
2871
2872
2875
2876
2878
2879
2881
2883
2884
2885
2887
2888
2889
2891
2895
2897
2901
2902
2903
2904
2907
2910
2911
2916


5822
5824
5825
5826
5827
5828
5829
5830
5831
5833
5834
5835
5836
5837
5841
5843
5851
5854
5856
5858
5859
5860
5862
5863
5864
5867
5869
5870
5875
5876
5877
5878
5881
5882
5885
5886
5890
5893
5894
5895
5897
5899
5900
5902
5903
5905
5922
5923
5924
5926
5927
5928
5929
5930
5933
5934
5935
5936
5939
5940
5941
5942
5952
5953
5955
5956
5957
5958
5959
5960
5961
5964
5965
5966
5985
5988
5990
5991
5992
5993
5994
5996
5997
5998
5999
6000
6003
6004
6005
6006
6007
6008
6009
6010
6017
6020
6021
6022
6023
6024
6036
6037
6038
6039
6040
6041
6042
6044
6045
6046
6047
6049
6050
6052
6053
6054
6068
6085
6086
6087
6088
6090
6109
6112
6117
6118
6119
6121
6122
6124
6125
6129
6130
6132
6137
6146
6152
6153
6187
6191
6194
6197
6201
6202
6203
6205
6209
6210
6215
6219
6221
6226
6228
6230
6231
6232
6233
6235
6240
6245
6249
6250
6251
6253
6263
6266
6268
6270
6272
6281
6282
6283
6284
6333
6338
6339
6342
6346
6350
6351
6352
6353
6355
6360
6363
6364
6365
6366
6367
6368
6374
6375
6380
6381
6383
6386
6387
6388
6395
6397


10765
10769
10776
10780
10783
10785
10788
10789
10793
10797
10799
10802
10805
10807
10808
10809
10811
10813
10814
10815
10816
10819
10820
10822
10829
10831
10836
10842
10845
10855
10869
10878
10880
10884
10885
10889
10890
10893
10898
10904
10906
10908
10912
10914
10915
10916
10917
10925
10934
10946
10947
10949
10960
10962
10964
10966
10968
10971
10973
10986
10989
10995
10996
10997
10998
10999
11001
11002
11011
11017
11027
11028
11030
11037
11038
11047
11050
11052
11054
11056
11057
11060
11071
11081
11083
11084
11085
11091
11093
11096
11104
11106
11110
11111
11112
11113
11115
11116
11121
11122
11124
11125
11126
11127
11129
11131
11132
11135
11136
11138
11139
11147
11149
11159
11160
11161
11166
11167
11168
11170
11177
11179
11182
11187
11188
11195
11200
11202
11208
11215
11229
11231
11235
11241
11248
11253
11258
11262
11265
11269
11274
11278
11283
11284
11287
11289
11292
11293
11320
11330
11339
11347
11351
11357
11370
11373
11385
11388
11393
11394
11396
11399
11402
11404
11407
11408
1141

18867
18870
18875
18876
18880
18881
18885
18887
18891
18901
18902
18905
18907
18908
18913
18919
18931
18932
18945
18946
18961
18963
18966
18968
18975
18983
18985
19000
19001
19009
19027
19028
19030
19036
19039
19040
19044
19046
19048
19056
19062
19074
19081
19083
19100
19114
19115
19120
19127
19145
19161
19184
19186
19187
19188
19201
19212
19237
19246
19253
19257
19272
19274
19301
19304
19307
19329
19348
19349
19351
19358
19361
19363
19368
19370
19372
19377
19378
19379
19381
19392
19399
19409
19414
19416
19417
19418
19419
19425
19427
19432
19442
19447
19456
19464
19466
19475
19478
19484
19498
19505
19508
19512
19513
19526
19530
19531
19534
19537
19540
19544
19552
19554
19560
19571
19578
19591
19600
19614
19616
19621
19622
19623
19624
19630
19633
19634
19643
19646
19647
19650
19651
19653
19665
19671
19676
19679
19696
19697
19725
19727
19732
19735
19763
19764
19765
19766
19777
19793
19796
19802
19803
19811
19834
19841
19842
19854
19857
19876
19877
19878
19888
19902
19903
19904
19908
1990

...

207351
207370
207378
207398
207442
207486
207487
207568
207572
207602
207653
207670
207687
207691
207713
207719
207729
207753
207764
207783
207796
207809
207814
207830
207845
207848
207883
207898
207899
207905
207910
207911
207917
207919
207951
207965
207975
207987
207991
208023
208024
208073
208093
208134
208170
208217
208256
208316
208321
208323
208337
208340
208360
208377
208411
208419
208428
208480
208533
208543
208583
208661
208663
208670
208700
208736
208754
208766
208773
208775
208800
208801
208804
208807
208808
208887
208888
208895
208918
208995
209001
209003
209010
209014
209033
209053
209090
209095
209113
209136
209166
209168
209190
209206
209220
209222
209225
209280
209282
209283
209284
209289
209290
209320
209322
209324
209325
209344
209366
209378
209383
209418
209423
209447
209450
209452
209488
209506
209511
209530
209538
209541
209542
209551
209567
209578
209641
209642
209644
209649
209653
209660
209661
209664
209667
209671
209672
209685
209696
209714
209716
209734
209737

231315
231316
231327
231331
231362
231367
231368
231392
231450
231457
231476
231477
231484
231538
231553
231554
231559
231567
231573
231574
231575
231581
231587
231611
231618
231620
231624
231639
231644
231664
231665
231666
231674
231683
231696
231733
231748
231801
231812
231819
231824
231837
231854
231872
231876
231878
231920
231939
231942
231954
231960
231962
231966
231972
231991
231999
232041
232043
232045
232078
232079
232090
232119
232134
232139
232162
232166
232201
232210
232216
232219
232238
232242
232250
232254
232267
232300
232303
232318
232345
232348
232351
232353
232358
232361
232385
232403
232405
232412
232414
232417
232420
232437
232446
232473
232478
232481
232509
232510
232520
232524
232595
232661
232666
232732
232800
232822
232823
232824
232827
232829
232830
232831
232832
232874
232894
232895
232900
232918
232924
232944
232950
232956
232974
232979
232980
232981
232988
233006
233015
233016
233018
233020
233033
233048
233070
233078
233080
233085
233094
233144
233149
233194

253618
253635
253652
253664
253679
253684
253696
253705
253719
253743
253756
253763
253766
253786
253807
253819
253861
253862
254017
254018
254025
254029
254088
254110
254123
254132
254135
254138
254145
254149
254157
254178
254188
254189
254192
254193
254195
254213
254226
254227
254230
254239
254322
254341
254386
254394
254399
254415
254417
254419
254427
254494
254498
254513
254532
254546
254585
254588
254591
254613
254617
254618
254619
254634
254639
254640
254681
254683
254686
254695
254708
254713
254743
254759
254846
254888
254894
254923
254936
254938
254976
254992
254994
255013
255020
255027
255029
255034
255037
255042
255165
255171
255175
255227
255235
255249
255255
255262
255272
255291
255293
255310
255332
255335
255356
255360
255363
255381
255392
255393
255396
255455
255456
255478
255484
255507
255516
255524
255570
255586
255594
255597
255608
255615
255618
255633
255635
255639
255640
255642
255651
255653
255658
255659
255664
255668
255674
255675
255678
255680
255683
255692
255695

276801
276817
276830
276832
276856
276880
276894
276923
276924
276925
276997
277003
277017
277018
277030
277035
277061
277080
277085
277109
277131
277184
277405
277410
277424
277434
277448
277458
277469
277475
277481
277538
277565
277597
277611
277629
277659
277662
277671
277672
277699
277700
277779
277892
277901
277902
277903
277927
277930
277931
277980
278042
278120
278139
278142
278218
278292
278297
278304
278305
278322
278359
278373
278402
278413
278484
278553
278554
278693
278751
278783
278824
278971
278989
279014
279056
279087
279135
279198
279204
279254
279306
279307
279328
279348
279419
279497
279527
279537
279556
279581
279613
279643
279644
279646
279649
279720
279727
279741
279776
279869
279884
279900
279911
279928
279931
279967
279975
279996
280032
280041
280106
280107
280131
280132
280136
280143
280148
280149
280162
280201
280202
280203
280281
280282
280304
280378
280430
280453
280475
280480
280501
280566
280575
280655
280729
280730
280742
280748
280789
280794
280811
280812

307963
307971
307997
308028
308119
308126
308329
308354
308357
308368
308385
308386
308388
308416
308493
308500
308529
308532
308565
308566
308621
308652
308755
308762
308765
308870
308948
308970
308989
309000
309003
309081
309105
309109
309110
309113
309129
309207
309250
309297
309319
309341
309408
309430
309545
309600
309630
309752
309857
309862
309917
310031
310076
310100
310192
310194
310196
310198
310203
310363
310408
310442
310448
310578
310610
310611
310612
310632
310641
310726
310779
310789
310846
310873
310880
310885
310888
310953
310968
311004
311020
311191
311192
311193
311209
311322
311330
311464
311465
311659
311686
311702
311708
311715
311751
311828
311829
311894
311918
311990
312059
312182
312251
312259
312267
312289
312318
312346
312372
312463
312484
312594
312613
312618
312626
312726
312738
312744
312762
312767
312786
312804
312904
312951
312965
312968
313000
313002
313008
313010
313085
313090
313100
313129
313163
313178
313261
313262
313269
313274
313292
313349
313352

In [38]:
#ratings_distribution = pd.read_pickle('data_cleaned/ratings_distribution.pkl')

In [55]:
ratings_distribution.set_axis(list(raw_ratings.keys()), axis=0, inplace=True)

In [56]:
ratings_distribution.head()

0 0.0  0.1  0.5  1.0  1.1  1.2  1.3  1.4  1.5  1.6  1.7  1.8  1.9   2.0  2.1   \
1  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  23.0  NaN   
2  NaN  NaN  NaN  3.0  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN   2.0  NaN   
3  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN   NaN  NaN   
4  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN   NaN  NaN   
5  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN   NaN  NaN   

0 2.2  2.3  2.4  2.5  2.6  2.7  2.8  2.9   3.0  3.1  3.2  3.3  3.4  3.5  3.6   \
1  NaN  NaN  NaN  1.0  NaN  NaN  NaN  NaN  53.0  1.0  NaN  NaN  1.0  5.0  NaN   
2  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN   8.0  NaN  NaN  NaN  NaN  1.0  NaN   
3  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  13.0  NaN  NaN  NaN  NaN  1.0  NaN   
4  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN   5.0  NaN  NaN  NaN  NaN  NaN  NaN   
5  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN   NaN  NaN  NaN  NaN  NaN  NaN  NaN   

0 3.7  3.8  3.9    4.0  4.1  4.2  4.3  4.4   4.5  4.6  4.7  4.8  4.9    5.0   \
1  NaN  NaN  NaN   85.0  NaN  NaN  NaN  NaN   7.0  NaN  NaN  NaN  NaN  212.0   
2  NaN  NaN  NaN   18.0  NaN  NaN  NaN  NaN   1.0  NaN  NaN  NaN  NaN   65.0   
3  NaN  2.0  NaN  150.0  NaN  2.0  NaN  1.0  12.0  NaN  1.0  4.0  NaN  454.0   
4  NaN  NaN  NaN    9.0  NaN  NaN  NaN  NaN   1.0  NaN  NaN  NaN  NaN   39.0   
5  NaN  NaN  NaN   35.0  NaN  1.0  2.0  1.0  17.0  NaN  NaN  NaN  NaN  819.0   

0 5.1  5.2  5.3  5.4   5.5  5.6  5.7   5.8  5.9     6.0  6.1   6.2   6.3   \
1  NaN  NaN  NaN  NaN  15.0  NaN  1.0   1.0  2.0   513.0  3.0   4.0   2.0   
2  1.0  NaN  NaN  NaN   8.0  NaN  NaN   1.0  NaN   140.0  2.0   NaN   NaN   
3  1.0  2.0  2.0  NaN  36.0  1.0  1.0   8.0  1.0  1564.0  2.0   5.0   7.0   
4  NaN  NaN  NaN  NaN   5.0  NaN  NaN   NaN  NaN    88.0  NaN   NaN   NaN   
5  1.0  5.0  2.0  4.0  82.0  5.0  7.0  17.0  3.0  2352.0  7.0  18.0  12.0   

0  6.4    6.5   6.6   6.7   6.8   6.9     7.0   7.1   7.2   7.3   7.4   \
1   6.0   76.0   NaN   6.0  11.0   7.0   986.0   3.0  19.0   4.0   4.0   
2   NaN   14.0   2.0   2.0   2.0   NaN   142.0   1.0   1.0   NaN   NaN   
3   8.0  367.0   7.0  13.0  46.0  20.0  3995.0  20.0  83.0  55.0  47.0   
4   NaN   19.0   NaN   NaN   1.0   1.0    94.0   NaN   2.0   NaN   1.0   
5  12.0  483.0  11.0  13.0  59.0  29.0  5039.0  28.0  98.0  53.0  59.0   

0    7.5   7.6   7.7    7.8   7.9     8.0   8.1   8.2   8.3   8.4    8.5   \
1   229.0   7.0   9.0   32.0  19.0  1265.0   6.0  34.0   9.0  10.0  225.0   
2    10.0   NaN   2.0    NaN   1.0    80.0   NaN   NaN   NaN   NaN    2.0   
3  1050.0  42.0  51.0  127.0  35.0  4091.0  40.0  56.0  23.0  22.0  486.0   
4     9.0   NaN   NaN    1.0   NaN    46.0   NaN   NaN   NaN   NaN    2.0   
5  1065.0  46.0  46.0  118.0  35.0  4300.0  24.0  64.0  21.0  25.0  446.0   

0  8.6   8.7   8.8   8.9     9.0   9.1   9.2  9.3   9.4   9.5  9.6  9.7   \
1  12.0  10.0  19.0   8.0   843.0   4.0  11.0  5.0  11.0  86.0  3.0  4.0   
2   NaN   NaN   1.0   NaN    32.0   NaN   NaN  1.0   NaN   1.0  NaN  NaN   
3  28.0  13.0  33.0  15.0  1497.0  11.0  20.0  7.0   4.0  77.0  3.0  1.0   
4   NaN   1.0   NaN   NaN    15.0   NaN   NaN  NaN   NaN   NaN  NaN  NaN   
5  14.0  17.0  32.0   9.0  1792.0  11.0  18.0  8.0   4.0  82.0  7.0  9.0   

0  9.8  9.9    10.0  
1   6.0  8.0  426.0  
2   1.0  NaN   17.0  
3   5.0  3.0  477.0  
4   NaN  NaN    3.0  
5  10.0  5.0  905.0

In [57]:
ratings_distribution.fillna(0, inplace=True)

In [58]:
ratings_distribution.head()

0 0.0  0.1  0.5  1.0  1.1  1.2  1.3  1.4  1.5  1.6  1.7  1.8  1.9   2.0  2.1   \
1  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  23.0  0.0   
2  0.0  0.0  0.0  3.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   2.0  0.0   
3  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   0.0  0.0   
4  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   0.0  0.0   
5  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   0.0  0.0   

0 2.2  2.3  2.4  2.5  2.6  2.7  2.8  2.9   3.0  3.1  3.2  3.3  3.4  3.5  3.6   \
1  0.0  0.0  0.0  1.0  0.0  0.0  0.0  0.0  53.0  1.0  0.0  0.0  1.0  5.0  0.0   
2  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   8.0  0.0  0.0  0.0  0.0  1.0  0.0   
3  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  13.0  0.0  0.0  0.0  0.0  1.0  0.0   
4  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   5.0  0.0  0.0  0.0  0.0  0.0  0.0   
5  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   0.0  0.0  0.0  0.0  0.0  0.0  0.0   

0 3.7  3.8  3.9    4.0  4.1  4.2  4.3  4.4   4.5  4.6  4.7  4.8  4.9    5.0   \
1  0.0  0.0  0.0   85.0  0.0  0.0  0.0  0.0   7.0  0.0  0.0  0.0  0.0  212.0   
2  0.0  0.0  0.0   18.0  0.0  0.0  0.0  0.0   1.0  0.0  0.0  0.0  0.0   65.0   
3  0.0  2.0  0.0  150.0  0.0  2.0  0.0  1.0  12.0  0.0  1.0  4.0  0.0  454.0   
4  0.0  0.0  0.0    9.0  0.0  0.0  0.0  0.0   1.0  0.0  0.0  0.0  0.0   39.0   
5  0.0  0.0  0.0   35.0  0.0  1.0  2.0  1.0  17.0  0.0  0.0  0.0  0.0  819.0   

0 5.1  5.2  5.3  5.4   5.5  5.6  5.7   5.8  5.9     6.0  6.1   6.2   6.3   \
1  0.0  0.0  0.0  0.0  15.0  0.0  1.0   1.0  2.0   513.0  3.0   4.0   2.0   
2  1.0  0.0  0.0  0.0   8.0  0.0  0.0   1.0  0.0   140.0  2.0   0.0   0.0   
3  1.0  2.0  2.0  0.0  36.0  1.0  1.0   8.0  1.0  1564.0  2.0   5.0   7.0   
4  0.0  0.0  0.0  0.0   5.0  0.0  0.0   0.0  0.0    88.0  0.0   0.0   0.0   
5  1.0  5.0  2.0  4.0  82.0  5.0  7.0  17.0  3.0  2352.0  7.0  18.0  12.0   

0  6.4    6.5   6.6   6.7   6.8   6.9     7.0   7.1   7.2   7.3   7.4   \
1   6.0   76.0   0.0   6.0  11.0   7.0   986.0   3.0  19.0   4.0   4.0   
2   0.0   14.0   2.0   2.0   2.0   0.0   142.0   1.0   1.0   0.0   0.0   
3   8.0  367.0   7.0  13.0  46.0  20.0  3995.0  20.0  83.0  55.0  47.0   
4   0.0   19.0   0.0   0.0   1.0   1.0    94.0   0.0   2.0   0.0   1.0   
5  12.0  483.0  11.0  13.0  59.0  29.0  5039.0  28.0  98.0  53.0  59.0   

0    7.5   7.6   7.7    7.8   7.9     8.0   8.1   8.2   8.3   8.4    8.5   \
1   229.0   7.0   9.0   32.0  19.0  1265.0   6.0  34.0   9.0  10.0  225.0   
2    10.0   0.0   2.0    0.0   1.0    80.0   0.0   0.0   0.0   0.0    2.0   
3  1050.0  42.0  51.0  127.0  35.0  4091.0  40.0  56.0  23.0  22.0  486.0   
4     9.0   0.0   0.0    1.0   0.0    46.0   0.0   0.0   0.0   0.0    2.0   
5  1065.0  46.0  46.0  118.0  35.0  4300.0  24.0  64.0  21.0  25.0  446.0   

0  8.6   8.7   8.8   8.9     9.0   9.1   9.2  9.3   9.4   9.5  9.6  9.7   \
1  12.0  10.0  19.0   8.0   843.0   4.0  11.0  5.0  11.0  86.0  3.0  4.0   
2   0.0   0.0   1.0   0.0    32.0   0.0   0.0  1.0   0.0   1.0  0.0  0.0   
3  28.0  13.0  33.0  15.0  1497.0  11.0  20.0  7.0   4.0  77.0  3.0  1.0   
4   0.0   1.0   0.0   0.0    15.0   0.0   0.0  0.0   0.0   0.0  0.0  0.0   
5  14.0  17.0  32.0   9.0  1792.0  11.0  18.0  8.0   4.0  82.0  7.0  9.0   

0  9.8  9.9    10.0  
1   6.0  8.0  426.0  
2   1.0  0.0   17.0  
3   5.0  3.0  477.0  
4   0.0  0.0    3.0  
5  10.0  5.0  905.0

In [59]:
ratings_distribution['total_ratings'] = ratings_distribution.sum(axis=1)

In [44]:
#ratings_distribution = ratings_distribution.T.reset_index().T

In [60]:
ratings_distribution.reset_index(inplace=True)

In [61]:
ratings_distribution.head()

0 index  0.0  0.1  0.5  1.0  1.1  1.2  1.3  1.4  1.5  1.6  1.7  1.8  1.9  \
0     1  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
1     2  0.0  0.0  0.0  3.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
2     3  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
3     4  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
4     5  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   

0   2.0  2.1  2.2  2.3  2.4  2.5  2.6  2.7  2.8  2.9   3.0  3.1  3.2  3.3  \
0  23.0  0.0  0.0  0.0  0.0  1.0  0.0  0.0  0.0  0.0  53.0  1.0  0.0  0.0   
1   2.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   8.0  0.0  0.0  0.0   
2   0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  13.0  0.0  0.0  0.0   
3   0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   5.0  0.0  0.0  0.0   
4   0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   0.0  0.0  0.0  0.0   

0  3.4  3.5  3.6  3.7  3.8  3.9    4.0  4.1  4.2  4.3  4.4   4.5  4.6  4.7  \
0  1.0  5.0  0.0  0.0  0.0  0.0   85.0  0.0  0.0  0.0  0.0   7.0  0.0  0.0   
1  0.0  1.0  0.0  0.0  0.0  0.0   18.0  0.0  0.0  0.0  0.0   1.0  0.0  0.0   
2  0.0  1.0  0.0  0.0  2.0  0.0  150.0  0.0  2.0  0.0  1.0  12.0  0.0  1.0   
3  0.0  0.0  0.0  0.0  0.0  0.0    9.0  0.0  0.0  0.0  0.0   1.0  0.0  0.0   
4  0.0  0.0  0.0  0.0  0.0  0.0   35.0  0.0  1.0  2.0  1.0  17.0  0.0  0.0   

0  4.8  4.9    5.0  5.1  5.2  5.3  5.4   5.5  5.6  5.7   5.8  5.9     6.0  \
0  0.0  0.0  212.0  0.0  0.0  0.0  0.0  15.0  0.0  1.0   1.0  2.0   513.0   
1  0.0  0.0   65.0  1.0  0.0  0.0  0.0   8.0  0.0  0.0   1.0  0.0   140.0   
2  4.0  0.0  454.0  1.0  2.0  2.0  0.0  36.0  1.0  1.0   8.0  1.0  1564.0   
3  0.0  0.0   39.0  0.0  0.0  0.0  0.0   5.0  0.0  0.0   0.0  0.0    88.0   
4  0.0  0.0  819.0  1.0  5.0  2.0  4.0  82.0  5.0  7.0  17.0  3.0  2352.0   

0  6.1   6.2   6.3   6.4    6.5   6.6   6.7   6.8   6.9     7.0   7.1   7.2  \
0  3.0   4.0   2.0   6.0   76.0   0.0   6.0  11.0   7.0   986.0   3.0  19.0   
1  2.0   0.0   0.0   0.0   14.0   2.0   2.0   2.0   0.0   142.0   1.0   1.0   
2  2.0   5.0   7.0   8.0  367.0   7.0  13.0  46.0  20.0  3995.0  20.0  83.0   
3  0.0   0.0   0.0   0.0   19.0   0.0   0.0   1.0   1.0    94.0   0.0   2.0   
4  7.0  18.0  12.0  12.0  483.0  11.0  13.0  59.0  29.0  5039.0  28.0  98.0   

0   7.3   7.4     7.5   7.6   7.7    7.8   7.9     8.0   8.1   8.2   8.3  \
0   4.0   4.0   229.0   7.0   9.0   32.0  19.0  1265.0   6.0  34.0   9.0   
1   0.0   0.0    10.0   0.0   2.0    0.0   1.0    80.0   0.0   0.0   0.0   
2  55.0  47.0  1050.0  42.0  51.0  127.0  35.0  4091.0  40.0  56.0  23.0   
3   0.0   1.0     9.0   0.0   0.0    1.0   0.0    46.0   0.0   0.0   0.0   
4  53.0  59.0  1065.0  46.0  46.0  118.0  35.0  4300.0  24.0  64.0  21.0   

0   8.4    8.5   8.6   8.7   8.8   8.9     9.0   9.1   9.2  9.3   9.4   9.5  \
0  10.0  225.0  12.0  10.0  19.0   8.0   843.0   4.0  11.0  5.0  11.0  86.0   
1   0.0    2.0   0.0   0.0   1.0   0.0    32.0   0.0   0.0  1.0   0.0   1.0   
2  22.0  486.0  28.0  13.0  33.0  15.0  1497.0  11.0  20.0  7.0   4.0  77.0   
3   0.0    2.0   0.0   1.0   0.0   0.0    15.0   0.0   0.0  0.0   0.0   0.0   
4  25.0  446.0  14.0  17.0  32.0   9.0  1792.0  11.0  18.0  8.0   4.0  82.0   

0  9.6  9.7   9.8  9.9   10.0 total_ratings  
0  3.0  4.0   6.0  8.0  426.0        5352.0  
1  0.0  0.0   1.0  0.0   17.0         562.0  
2  3.0  1.0   5.0  3.0  477.0       15148.0  
3  0.0  0.0   0.0  0.0    3.0         342.0  
4  7.0  9.0  10.0  5.0  905.0       18387.0

In [62]:
ratings_distribution.rename(columns={'index':'BGGId'}, inplace=True)

In [63]:
ratings_distribution['BGGId'] = ratings_distribution['BGGId'].astype('int64')

In [64]:
ratings_distribution.head()

0 BGGId  0.0  0.1  0.5  1.0  1.1  1.2  1.3  1.4  1.5  1.6  1.7  1.8  1.9  \
0     1  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
1     2  0.0  0.0  0.0  3.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
2     3  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
3     4  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
4     5  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   

0   2.0  2.1  2.2  2.3  2.4  2.5  2.6  2.7  2.8  2.9   3.0  3.1  3.2  3.3  \
0  23.0  0.0  0.0  0.0  0.0  1.0  0.0  0.0  0.0  0.0  53.0  1.0  0.0  0.0   
1   2.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   8.0  0.0  0.0  0.0   
2   0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  13.0  0.0  0.0  0.0   
3   0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   5.0  0.0  0.0  0.0   
4   0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   0.0  0.0  0.0  0.0   

0  3.4  3.5  3.6  3.7  3.8  3.9    4.0  4.1  4.2  4.3  4.4   4.5  4.6  4.7  \
0  1.0  5.0  0.0  0.0  0.0  0.0   85.0  0.0  0.0  0.0  0.0   7.0  0.0  0.0   
1  0.0  1.0  0.0  0.0  0.0  0.0   18.0  0.0  0.0  0.0  0.0   1.0  0.0  0.0   
2  0.0  1.0  0.0  0.0  2.0  0.0  150.0  0.0  2.0  0.0  1.0  12.0  0.0  1.0   
3  0.0  0.0  0.0  0.0  0.0  0.0    9.0  0.0  0.0  0.0  0.0   1.0  0.0  0.0   
4  0.0  0.0  0.0  0.0  0.0  0.0   35.0  0.0  1.0  2.0  1.0  17.0  0.0  0.0   

0  4.8  4.9    5.0  5.1  5.2  5.3  5.4   5.5  5.6  5.7   5.8  5.9     6.0  \
0  0.0  0.0  212.0  0.0  0.0  0.0  0.0  15.0  0.0  1.0   1.0  2.0   513.0   
1  0.0  0.0   65.0  1.0  0.0  0.0  0.0   8.0  0.0  0.0   1.0  0.0   140.0   
2  4.0  0.0  454.0  1.0  2.0  2.0  0.0  36.0  1.0  1.0   8.0  1.0  1564.0   
3  0.0  0.0   39.0  0.0  0.0  0.0  0.0   5.0  0.0  0.0   0.0  0.0    88.0   
4  0.0  0.0  819.0  1.0  5.0  2.0  4.0  82.0  5.0  7.0  17.0  3.0  2352.0   

0  6.1   6.2   6.3   6.4    6.5   6.6   6.7   6.8   6.9     7.0   7.1   7.2  \
0  3.0   4.0   2.0   6.0   76.0   0.0   6.0  11.0   7.0   986.0   3.0  19.0   
1  2.0   0.0   0.0   0.0   14.0   2.0   2.0   2.0   0.0   142.0   1.0   1.0   
2  2.0   5.0   7.0   8.0  367.0   7.0  13.0  46.0  20.0  3995.0  20.0  83.0   
3  0.0   0.0   0.0   0.0   19.0   0.0   0.0   1.0   1.0    94.0   0.0   2.0   
4  7.0  18.0  12.0  12.0  483.0  11.0  13.0  59.0  29.0  5039.0  28.0  98.0   

0   7.3   7.4     7.5   7.6   7.7    7.8   7.9     8.0   8.1   8.2   8.3  \
0   4.0   4.0   229.0   7.0   9.0   32.0  19.0  1265.0   6.0  34.0   9.0   
1   0.0   0.0    10.0   0.0   2.0    0.0   1.0    80.0   0.0   0.0   0.0   
2  55.0  47.0  1050.0  42.0  51.0  127.0  35.0  4091.0  40.0  56.0  23.0   
3   0.0   1.0     9.0   0.0   0.0    1.0   0.0    46.0   0.0   0.0   0.0   
4  53.0  59.0  1065.0  46.0  46.0  118.0  35.0  4300.0  24.0  64.0  21.0   

0   8.4    8.5   8.6   8.7   8.8   8.9     9.0   9.1   9.2  9.3   9.4   9.5  \
0  10.0  225.0  12.0  10.0  19.0   8.0   843.0   4.0  11.0  5.0  11.0  86.0   
1   0.0    2.0   0.0   0.0   1.0   0.0    32.0   0.0   0.0  1.0   0.0   1.0   
2  22.0  486.0  28.0  13.0  33.0  15.0  1497.0  11.0  20.0  7.0   4.0  77.0   
3   0.0    2.0   0.0   1.0   0.0   0.0    15.0   0.0   0.0  0.0   0.0   0.0   
4  25.0  446.0  14.0  17.0  32.0   9.0  1792.0  11.0  18.0  8.0   4.0  82.0   

0  9.6  9.7   9.8  9.9   10.0 total_ratings  
0  3.0  4.0   6.0  8.0  426.0        5352.0  
1  0.0  0.0   1.0  0.0   17.0         562.0  
2  3.0  1.0   5.0  3.0  477.0       15148.0  
3  0.0  0.0   0.0  0.0    3.0         342.0  
4  7.0  9.0  10.0  5.0  905.0       18387.0

In [65]:
games = pd.read_pickle('data_dirty/games.pkl')
games.head()

BGGId            Name                                        Description  \
0     1      Die Macher  Die Macher is a game about seven sequential po...   
1     2    Dragonmaster  Dragonmaster is a trick-taking card game based...   
2     3         Samurai  Samurai is set in medieval Japan. Players comp...   
3     4  Tal der Könige  When you see the triangular box and the luxuri...   
4     5         Acquire  In Acquire, each player strategically invests ...   

  YearPublished  GameWeight  AvgRating  BayesAvgRating   StdDev MinPlayers  \
0          1986      4.3206    7.61428         7.10363  1.57979          3   
1          1981      1.9630    6.64537         5.78447  1.45440          3   
2          1998      2.4859    7.45601         7.23994  1.18227          2   
3          1992      2.6667    6.60006         5.67954  1.23129          2   
4          1964      2.5031    7.33861         7.14189  1.33583          2   

  MaxPlayers  ComAgeRec  LanguageEase BestPlayers GoodPlayers NumOwned  \
0          5  14.366667      1.395833           5      [4, 5]     7498   
1          4        NaN     27.000000        None          []     1285   
2          4   9.307692      1.000000           3   [2, 3, 4]    15578   
3          4  13.000000    256.000000        None          []      638   
4          6  11.410256     21.152941           4   [3, 4, 5]    23735   

  NumWant NumWish NumWeightVotes MfgPlaytime ComMinPlaytime ComMaxPlaytime  \
0     501    2039            761         240            240            240   
1      72     191             54          30             30             30   
2     799    3450           1451          60             30             60   
3      54     123             30          60             60             60   
4     548    2671           1606          90             90             90   

  MfgAgeRec NumUserRatings NumComments NumAlternates NumExpansions  \
0        14           5354         NaN             2             0   
1        12            562         NaN             0             0   
2        10          15146         NaN             6             0   
3        12            340         NaN             0             0   
4        12          18655         NaN             6             2   

  NumImplementations IsReimplementation                         Family  \
0                  0                  0    Classic Line (Valley Games)   
1                  2                  1                            NaN   
2                  1                  0  Euro Classics (Reiner Knizia)   
3                  0                  0                            NaN   
4                  0                  0                   3M Bookshelf   

     Theme Category Kickstarted  \
0      NaN      NaN         NaN   
1      NaN      NaN         NaN   
2  Samurai      NaN         NaN   
3      NaN      NaN         NaN   
4      NaN      NaN         NaN   

                                           ImagePath NumAwards NumFans  \
0  https://cf.geekdo-images.com/rpwCZAjYLD940NWwP...       NaN     NaN   
1  https://cf.geekdo-images.com/oQYhaJx5Lg3KcGis2...       NaN     NaN   
2  https://cf.geekdo-images.com/o9-sNXmFS_TLAb7Zl...       NaN     NaN   
3  https://cf.geekdo-images.com/nYiYhUlatT2DpyXaJ...       NaN     NaN   
4  https://cf.geekdo-images.com/3C--kJRhi6kTPHsr9...       NaN     NaN   

  NumPageViews RulesPosts TotalPosts IsExpansion  Rank:boardgame  \
0          NaN        NaN        NaN         NaN           316.0   
1          NaN        NaN        NaN         NaN          3993.0   
2          NaN        NaN        NaN         NaN           224.0   
3          NaN        NaN        NaN         NaN          5345.0   
4          NaN        NaN        NaN         NaN           290.0   

   Rank:strategygames  Rank:abstracts  Rank:familygames  Rank:thematic  \
0               180.0             NaN               NaN            NaN   
1              1577.0             NaN               NaN            NaN 

In [66]:
ratings_distribution.to_pickle('data_cleaned/ratings_distribution.pkl')

# DEPRECATED

## Ratings Dist

In [ ]:
# open ratings distribution
ratings_dist = pd.read_pickle('data_dirty/ratings_dist.pkl')
ratings_dist.info()

In [ ]:
ratings_dist.drop_duplicates(subset='BGGId', keep='first', inplace=True) # drop duplicates
ratings_dist.fillna(0, inplace=True) # fill nan
ratings_dist.drop(ratings_dist.index[empty_games], inplace=True) # drop empty games
ratings_dist.reset_index(inplace=True, drop=True) # reset index
ratings_dist.drop(ratings_dist.index[not_released], inplace=True) # drop unreleased games
ratings_dist.reset_index(inplace=True, drop=True) # reset index

# for each column:
for column in ratings_dist.columns[1:]:
    # fix numbers as needed (convert 1xk to 10000)
    ratings_dist[column] = ratings_dist[column].apply(lambda x: fix_numbers(x))

# add a column
ratings_dist['num_votes'] = games['NumUserRatings']

# convert types to int32
temp_id = ratings_dist['BGGId']
ratings_dist.drop('BGGId', axis=1, inplace=True)
ratings_dist = ratings_dist.astype('int32')
ratings_dist['BGGId'] = temp_id

ratings_dist.info() # check memory usage

In [ ]:
# save to file
ratings_dist.to_pickle('data_cleaned_new_scraper/ratings_dist.pkl')

## Comments

In [ ]:
# load comments
comments = pd.read_pickle('data_dirty/comments.pkl')
comments.info()

In [ ]:
comments.drop_duplicates(subset=['BGGId', 'Username'], keep='first', inplace=True) # drop duplicates
comments.reset_index(inplace=True, drop=True) # rest index
comments.fillna(0, inplace=True) # fill na

# clean the comments text
comments['cleaned'] = comments['Value'].apply(lambda x: text_block_processor(x))
    
# drop the description field 
comments.drop('Value', axis=1, inplace=True)

In [ ]:
# save file
comments.to_pickle('data_cleaned_new_scraper/comments.pkl')

## Ratings Matrix

In [20]:
files = []

for item in os.listdir('data_dirty/pulled_ratings/'):
    files.append(item)

In [ ]:
# create a ratings matrix file from a set of files on disk
ratings_matrix = create_ratings_file(51,57, game_ids)

In [ ]:
# save file to pickle, specify filename carefully!
ratings_matrix.to_pickle('data_cleaned_new_scraper/ratings_matrix_cleaned_06.pkl')

### Data Validation

In [ ]:
ratings_matrix_1 = pd.read_pickle('userid/user_ratings31.pkl')
ratings_matrix_2  = pd.read_pickle('userid/user_ratings32.pkl')

In [ ]:
this_user = pd.DataFrame(ratings_matrix_1.T['Threnody'].dropna(axis=0))
this_user.rename(columns={'Threnody':'Rating'}, inplace=True)
this_user.reset_index(inplace=True)
this_user['Game'] = this_user['index'].astype('int32').map(game_id_lookup)
this_user.drop('index', axis=1, inplace=True)
this_user.sort_values('Rating', ascending=False).head(30)

In [ ]:
# create a ratings matrix file from a set of files on disk
ratings_matrix = create_ratings_file(31,32, game_ids)

In [ ]:
ratings_matrix.head()

In [ ]:
this_user = pd.DataFrame(ratings_matrix.T['Threnody'].dropna(axis=0))
this_user.rename(columns={'Threnody':'Rating'}, inplace=True)
this_user.reset_index(inplace=True)
this_user['Game'] = this_user['index'].astype('int32').map(game_id_lookup)
this_user.drop('index', axis=1, inplace=True)
this_user.sort_values('Rating', ascending=False).head(30)

In [ ]:
# save file to pickle, specify filename carefully!
ratings_matrix.to_pickle('data_cleaned_new_scraper/ratings_matrix_cleaned_06.pkl')

In [ ]:
del ratings_matrix
gc.collect()